## Investigate "collision protection volume" concept

In [1]:
%matplotlib inline
%reload_ext autoreload
%autoreload

In [2]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os

import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
import plotly.io as pio

### Load data
Load data from the `./data/interim/` folder and parse into `pandas` dataframes.

In [3]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_profile_features = df_from_csv('profile_features.csv', index_col=[0])

impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }

twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}

print('Done!')

Importing profiles.csv


C:\Users\z5189959\Desktop\nsw-2016-storm-impact\.venv\lib\site-packages\numpy\lib\arraysetops.py:522: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



Importing profile_features.csv
Importing impacts_forecasted_foreshore_slope_sto06.csv
Importing impacts_forecasted_mean_slope_sto06.csv
Importing impacts_observed.csv
Importing twl_foreshore_slope_sto06.csv
Importing twl_mean_slope_sto06.csv
Done!


Lets define a function to calculate the "collision protection volume" based on prestorm profiles.

### Get berm feature functions
Define a couple of functions which are going to help us get features of our berms.

In [27]:
from shapely.geometry import Point, LineString, Polygon


def collision_protection_vol(x, z, d_low_x, d_low_z, lower_z, angle):
    # First, get the bounding line strings of our protection volume
    lower_line = LineString([Point(min(x), lower_z), Point(max(x), lower_z)])
    profile_line = LineString([Point(x_coord, z_coord) for x_coord, z_coord in zip(x, z)
                               if all([not np.isnan(x_coord), not np.isnan(z_coord)])])
    slope_line = LineString([Point(d_low_x, d_low_z),
                             Point(max(x), d_low_z - max(x) * np.sin(np.deg2rad(angle)))])

    # Work out where our lower line and slope line intersect
    lower_profile_intersection = lower_line.intersection(profile_line)
    d_protected_intersection = lower_line.intersection(slope_line)

    # Define the perimeter of the protection area
    profile_protected = LineString([Point(x_coord, z_coord) for x_coord, z_coord
                                    in zip(profile_line.xy[0], profile_line.xy[1])
                                    if d_low_x < x_coord < lower_profile_intersection.xy[0][0]]
                                   + [lower_profile_intersection]
                                   + [d_protected_intersection]
                                   + [Point(d_low_x, d_low_z)])

    # Convert to polygon and return the area (m3/m)
    protection_area_poly = Polygon(profile_protected)
    protection_area_vol = protection_area_poly.area
    return protection_area_vol


def get_berm_width(z, d_low_x):
    """
    Returns the width of the berm, defined by the distance between dune toe to z=0
    """
    x_seaward_limit = z.dropna().tail(1).reset_index().x[0]
    return x_seaward_limit - d_low_x




site_id = 'NARRA0018'
profile_type = 'prestorm'
query = "site_id == '{}' and profile_type == '{}'".format(
    site_id, profile_type)
prestorm_profile = df_profiles.query(query)
profile_features = df_profile_features.query(query)

x = prestorm_profile.index.get_level_values('x')
z = prestorm_profile.z
d_low_x = profile_features.dune_toe_x.tolist()[0]
d_low_z = profile_features.dune_toe_z.tolist()[0]
angle = 60  # degrees from the horizontal
lower_z = 0.5  # from mhw

vol = collision_protection_vol(x, z, d_low_x, d_low_z, lower_z, angle)
berm_width = get_berm_width(z, d_low_x)

In [5]:
from datetime import timedelta

def wl_time(t, wl, z_lower, z_upper):
    """
    Returns the amount of time the water level is between two elevations.
    """
    df_wl = pd.DataFrame.from_records([(t_val, R2_val) for t_val, R2_val in zip(t,R2)], columns=['datetime','wl'])
    df_wl.set_index(pd.DatetimeIndex(df_wl['datetime']),inplace=True)
    df_wl.drop(columns=['datetime'], inplace=True)
    
    # Assumes that each record is one hour... probably need to check this
    hours = len(df_wl.query('{} < wl < {}'.format(z_lower, z_upper)))
    return timedelta(hours=hours)

def wave_power(t, wl, z_lower, z_upper, Hs0, Tp):
    """
    Returns the cumulative wave power when the water level is between two elevations.
    """
    df_wl = pd.DataFrame.from_records([(t_val, R2_val,Hs0_val,Tp_val) for t_val, R2_val,Hs0_val,Tp_val in zip(t,R2,Hs0,Tp)], columns=['datetime','wl', 'Hs0','Tp'])
    df_wl.set_index(pd.DatetimeIndex(df_wl['datetime']),inplace=True)
    df_wl.drop(columns=['datetime'], inplace=True)
    
    # Assumes that each record is one hour... probably need to check this
    rho = 1025 # kg/m3
    g = 9.8 # m/s2
    df_wl_times = df_wl.query('{} < wl < {}'.format(z_lower, z_upper))
    power = rho * g ** 2 / 64 / np.pi * df_wl_times.Hs0 ** 2 * df_wl_times.Tp
    return power.sum()

df_twl = twls['forecasted']['mean_slope_sto06']
df_twl_site = df_twl.query("site_id == '{}'".format(site_id))

R2 = df_twl_site.R2.tolist()
t = df_twl_site.index.get_level_values('datetime')
z_lower = 0.5
z_upper = d_low_z

exposed_time = wl_time(t, R2, z_lower,z_upper)

Hs0 = df_twl.Hs0.tolist()
Tp = df_twl.Tp.tolist()
wave_p = wave_power(t, R2, z_lower,z_upper,Hs0, Tp)


In [57]:
def dune_toe_elevation_change(site_id, df_profile_features):
    query = "site_id == '{}'".format(site_id)
    profile_features = df_profile_features.query(query)
    prestorm_dune_toe_z = profile_features.query("profile_type=='prestorm'").dune_toe_z.tolist()[0]
    poststorm_dune_toe_z = profile_features.query("profile_type=='poststorm'").dune_toe_z.tolist()[0]
    return prestorm_dune_toe_z - poststorm_dune_toe_z

toe_ele_change = dune_toe_elevation_change("MANNING0081", df_profile_features)
toe_ele_change

0.96

In [62]:
vols = []
exposed_times = []
toe_ele_changes = []
wave_powers = []
berm_widths = []
swash_vol_changes = []
dune_face_vol_changes = []
site_ids_to_plot = []

# Get site ids where we observed collision
observed_site_ids = impacts['observed'].query("storm_regime=='collision'").index.get_level_values('site_id').unique()

# # Get site ids where we forecast swash
# forecasted_site_ids = impacts['forecasted']['mean_slope_sto06'].query("storm_regime=='swash'").index.get_level_values('site_id').unique()

# site_ids = set(observed_site_ids).intersection(set(forecasted_site_ids))

site_ids = observed_site_ids

# Calculate for each site

for n, site_id in enumerate(site_ids):
    
    if n%20 ==0:
        print('{} of {}'.format(n, len(site_ids)))
    
    try:
        query = "site_id == '{}' and profile_type == '{}'".format(site_id, 'prestorm')
        prestorm_profile = df_profiles.query(query)
        profile_features = df_profile_features.query(query)

        vol = collision_protection_vol(x = prestorm_profile.index.get_level_values('x'),
                                       z = prestorm_profile.z,
                                       d_low_x = profile_features.dune_toe_x.tolist()[0],
                                       d_low_z = profile_features.dune_toe_z.tolist()[0],
                                       lower_z = profile_features.dune_toe_z.tolist()[0] - 2, # from mhw
                                       angle = 60,  # degrees from the horizontal
                                      )
        
        df_twl = twls['forecasted']['mean_slope_sto06']
        df_twl_site = df_twl.query("site_id == '{}'".format(site_id))
        
        berm_width = get_berm_width(z = prestorm_profile.z,
                                    d_low_x = profile_features.dune_toe_x.tolist()[0]) 
        
        exposed_time = wl_time(t = df_twl_site.index.get_level_values('datetime'),
                               wl = df_twl_site.R2.tolist(),
                               z_lower = profile_features.dune_toe_z.tolist()[0] -2,
                               z_upper = profile_features.dune_toe_z.tolist()[0],
                              )
        swash_vol_change = impacts['observed'].query("site_id == '{}'".format(site_id)).swash_vol_change.tolist()[0]
        dune_face_vol_change = impacts['observed'].query("site_id == '{}'".format(site_id)).dune_face_vol_change.tolist()[0]
        
        power = wave_power(t = df_twl_site.index.get_level_values('datetime'),
                           wl = df_twl_site.R2.tolist(),
                           z_lower = profile_features.dune_toe_z.tolist()[0] -2,
                           z_upper = profile_features.dune_toe_z.tolist()[0],
                           Hs0=df_twl_site.Hs0.tolist(),
                           Tp=df_twl_site.Tp.tolist())
        
        toe_ele_change = dune_toe_elevation_change(site_id, df_profile_features)
    except:
        continue
    
#     print(site_id, toe_ele_change)
    vols.append(vol)
    exposed_times.append(exposed_time)
    toe_ele_changes.append(toe_ele_change)
    wave_powers.append(power)
    berm_widths.append(berm_width)
    swash_vol_changes.append(swash_vol_change)
    dune_face_vol_changes.append(dune_face_vol_change)
    site_ids_to_plot.append(site_id)
    
    if n>100:
        break

    



0 of 816
20 of 816
40 of 816
60 of 816
80 of 816
100 of 816


In [72]:
trace1 = go.Scatter(
    x=berm_widths,
    y=dune_face_vol_changes,
    text = ['{}<br>{}'.format(ele, site_id) for ele,site_id in zip(toe_ele_changes,site_ids_to_plot)],
    mode='markers',
    marker=dict(
        size=4,
#         color = [-1 if x<0 else 1 for x in toe_ele_changes],
#         color =  toe_ele_changes,
#         color = dune_face_vol_changes,
#         color = [x.total_seconds() / 60 / 60 for x in exposed_times],
#         colorscale='Viridis',
#         showscale=True
    ))

layout = go.Layout(
    title='Dune Collision Protection',
#     height=300,
#     legend=dict(font={'size': 10}),
#     margin=dict(t=50, b=50, l=50, r=20),
    xaxis=dict(
        title='Berm width',
        autorange=True,
        showgrid=True,
        zeroline=True,
        showline=True,
    ),
    yaxis=dict(
        title='Dune face vol change',
        autorange=True,
        showgrid=True,
        zeroline=True,
        showline=True,
    ))

g_plot = go.FigureWidget(data=[trace1], layout=layout)
g_plot

FigureWidget({
    'data': [{'marker': {'size': 4},
              'mode': 'markers',
              'text': [-0…

In [51]:
# impacts['observed']
swash_vol_changes

[64.5799,
 21.0163,
 38.106,
 28.101,
 58.7247,
 33.5534,
 71.1675,
 52.6043,
 50.5765,
 39.9074,
 67.8385,
 43.9043,
 39.8181,
 37.7153,
 20.4454,
 39.7757,
 42.1843,
 33.6152,
 42.9587,
 39.9773,
 35.7835,
 31.2884,
 -0.4618,
 31.0094,
 33.3479,
 47.8394,
 32.3566,
 36.5205,
 45.7109,
 16.0687,
 35.4375,
 43.327,
 53.5016,
 31.0357,
 47.6528,
 25.5658,
 41.0514,
 28.1645,
 44.5443,
 42.925,
 33.9535,
 36.2626,
 35.2536]